# Import packages

In [43]:
import warnings
warnings.filterwarnings("ignore")

In [1]:
import pandas as pd
import numpy as np
from pypfopt.efficient_frontier import EfficientFrontier
from pypfopt import risk_models
from pypfopt.risk_models import CovarianceShrinkage
from pypfopt import expected_returns
from datetime import datetime
from pandas.tseries.offsets import BDay

In [2]:
import time
import pickle

In [3]:
fund_df = pd.read_csv('data_processor_update/sp500_fundamental_199601_202502.csv')

C:\Users\misss\AppData\Local\Temp\ipykernel_40368\3149756244.py:1: DtypeWarning: Columns (10,17,26,30) have mixed types. Specify dtype option on import or set low_memory=False.
  fund_df = pd.read_csv('data_processor_update/sp500_fundamental_199601_202502.csv')


In [4]:
fund_df.drop_duplicates('gvkey', inplace=True)
fund_df = fund_df[['gvkey','tic']]

# 1. Read Input Data

In [5]:
df_price = pd.read_csv("data_processor_update/sp500_price_199601_202502.csv")

In [6]:
df_price.shape

(4514910, 22)

In [7]:
df_price.columns

Index(['tic', 'cusip', 'permno', 'permco', 'issuno', 'hexcd', 'hsiccd', 'date',
       'bidlo', 'askhi', 'prc', 'adj_close_q', 'vol', 'ret', 'bid', 'ask',
       'shrout', 'cfacpr', 'cfacshr', 'openprc', 'numtrd', 'retx'],
      dtype='object')

In [8]:
# df_price['adj_price'] = df_price['prccd'] / df_price['ajexdi']
df_price['adj_price'] = df_price['adj_close_q']
df_price = pd.merge(df_price, fund_df, on='tic')
# df_price['gvkey'] = df_price['tic']
df_price['datadate'] = df_price['date']

In [9]:
df_price['datadate'] = df_price['datadate'].str[:10]

In [10]:
df_price = df_price[["gvkey", "datadate", 'adj_price']]

In [11]:
len(df_price.gvkey.unique())

741

In [12]:
selected_stock = pd.read_csv("stock_selected.csv",index_col=0)

In [13]:
selected_stock['trade_date'].unique().max(), selected_stock['trade_date'].unique().min()

('2024-12-02', '2001-03-01')

In [14]:
selected_stock=selected_stock[selected_stock.trade_date>='2004-03-01'].reset_index(drop=True)

In [15]:
selected_stock.shape

(16425, 3)

In [16]:
selected_stock.head()

gvkey  predicted_return  trade_date
0  162353          0.023077  2009-06-01
1  175138          0.023077  2009-06-01
2  178707          0.023077  2009-06-01
3  178901          0.025990  2009-06-01
4  178917          0.027077  2009-06-01

# 2. Get trade date

In [17]:
print("Number of unique stocks selected: ", len(selected_stock.gvkey.unique()))

Number of unique stocks selected:  697


In [18]:
all_date=df_price.datadate.unique()

In [19]:
len(all_date)

7325

In [20]:
trade_date=selected_stock.trade_date.unique()

In [21]:
trade_date

array(['2009-06-01', '2009-09-01', '2009-12-01', '2010-03-01',
       '2010-06-01', '2010-09-01', '2010-12-01', '2011-03-01',
       '2011-06-01', '2011-09-01', '2011-12-01', '2012-03-01',
       '2012-06-01', '2012-09-04', '2012-12-03', '2013-03-01',
       '2013-06-03', '2013-09-03', '2013-12-02', '2014-03-03',
       '2014-06-02', '2014-09-02', '2014-12-01', '2015-03-02',
       '2015-06-01', '2015-09-01', '2015-12-01', '2016-03-01',
       '2016-06-01', '2016-09-01', '2016-12-01', '2017-03-01',
       '2017-06-01', '2017-09-01', '2017-12-01', '2018-03-01',
       '2018-06-01', '2018-09-04', '2018-12-03', '2019-03-01',
       '2019-06-03', '2019-09-03', '2019-12-02', '2020-03-02',
       '2020-06-01', '2020-09-01', '2020-12-01', '2021-03-01',
       '2021-06-01', '2021-09-01', '2021-12-01', '2022-03-01',
       '2022-06-01', '2022-09-01', '2022-12-01', '2023-03-01',
       '2023-06-01', '2023-09-01', '2023-12-01', '2024-03-01',
       '2024-06-03', '2024-09-03', '2024-12-02', '2004-

In [22]:
print("Number of trade dates", len(trade_date))

Number of trade dates 84


# 3. Get daily 1 year return table in each 89 trade period

In [23]:
selected_stock.head()

gvkey  predicted_return  trade_date
0  162353          0.023077  2009-06-01
1  175138          0.023077  2009-06-01
2  178707          0.023077  2009-06-01
3  178901          0.025990  2009-06-01
4  178917          0.027077  2009-06-01

In [24]:
# took about 9 minutes to run
start = time.time()
all_return_table={}
#all_predicted_return={}
all_stocks_info = {}
#for i in range(0,1):
for i in range(len(trade_date)):
    #match trading date
    index = selected_stock.trade_date==trade_date[i]
    #get the corresponding trade period's selected stocks' name
    stocks_name=selected_stock.gvkey[selected_stock.trade_date==trade_date[i]].values
    temp_info = selected_stock[selected_stock.trade_date==trade_date[i]]
    temp_info = temp_info.reset_index()
    del temp_info['index']
    all_stocks_info[trade_date[i]] = temp_info
    #get the corresponding trade period's selected stocks' predicted return
    asset_expected_return=selected_stock[index].predicted_return.values
    
    
    #determine the business date
    #print(convert_to_yyyymmdd)
    tradedate = pd.to_datetime(trade_date[i])
    ts = datetime(tradedate.year-1, tradedate.month, tradedate.day)
    bd = pd.tseries.offsets.BusinessDay(n =1) 
    new_timestamp = ts - bd 
    all_date = pd.to_datetime(all_date, format="%Y-%m-%d")
    get_date_index=(all_date<tradedate) & (all_date>new_timestamp)
    get_date=all_date[get_date_index]
    #get adjusted price table
    return_table=pd.DataFrame()
    for m in range(len(stocks_name)):
        #get stocks's name
        index_tic=(df_price.gvkey==stocks_name[m])
        #get this stock's all historicall price from sp500_price
        sp500_temp=df_price[index_tic]
        merge_left_data_table = pd.DataFrame(get_date)
        merge_left_data_table.columns = ['datadate']
        #print(merge_left_data_table)
        sp500_temp.datadate = pd.to_datetime(sp500_temp.datadate, format="%Y-%m-%d")
        temp_price=merge_left_data_table.merge(sp500_temp, on=['datadate'], how='left')
        
        temp_price = temp_price.dropna()
        temp_price['daily_return']=temp_price.adj_price.pct_change()
        # return_table=return_table.append(temp_price,ignore_index=True)
        return_table = pd.concat([return_table,temp_price])
    all_return_table[trade_date[i]] = return_table
end = time.time()
print("Time consuming: ", (end-start)/60, " minutes")

C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2418609160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sp500_temp.datadate = pd.to_datetime(sp500_temp.datadate, format="%Y-%m-%d")
C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2418609160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sp500_temp.datadate = pd.to_datetime(sp500_temp.datadate, format="%Y-%m-%d")
C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2418609160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy

Time consuming:  1.8097829182942708  minutes


C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2418609160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sp500_temp.datadate = pd.to_datetime(sp500_temp.datadate, format="%Y-%m-%d")
C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2418609160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  sp500_temp.datadate = pd.to_datetime(sp500_temp.datadate, format="%Y-%m-%d")
C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2418609160.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy

In [25]:
check=all_stocks_info['2018-03-01'].gvkey.unique()

In [26]:
for i in check:
    if i not in all_return_table['2018-03-01'].gvkey.unique():
        print(i)

In [27]:
df_price.head()

gvkey    datadate  adj_price
0  126554  1999-11-18  26.511734
1  126554  1999-11-19  24.327538
2  126554  1999-11-22  26.511734
3  126554  1999-11-23  24.101578
4  126554  1999-11-24  24.741779

In [28]:
selected_stock[selected_stock.gvkey==34443]

gvkey  predicted_return  trade_date
1846  34443          0.037525  2020-09-01
1886  34443          0.025963  2021-03-01
1918  34443          0.027404  2021-06-01
1950  34443          0.029716  2021-09-01
2035  34443          0.020289  2023-09-01
2068  34443          0.011908  2024-06-03
2089  34443          0.013305  2024-09-03

In [29]:
df_price[df_price.gvkey==34443]

gvkey    datadate  adj_price
1113684  34443  2019-03-20  36.684479
1113685  34443  2019-03-21  36.080437
1113686  34443  2019-03-22  35.800518
1113687  34443  2019-03-25  36.205666
1113688  34443  2019-03-26  35.984673
...        ...         ...        ...
1115161  34443  2025-02-03  37.380001
1115162  34443  2025-02-04  38.549999
1115163  34443  2025-02-05  37.950001
1115164  34443  2025-02-06  38.770000
1115165  34443  2025-02-07  38.580002

[1482 rows x 3 columns]

## Save to pickle

In [30]:
with open('all_return_table.pickle', 'wb') as handle: 
    pickle.dump(all_return_table, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [31]:
with open('all_stocks_info.pickle', 'wb') as handle:
    pickle.dump(all_stocks_info, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [32]:
with open('all_return_table.pickle', 'rb') as handle:
    all_return_table = pickle.load(handle)

with open('all_stocks_info.pickle', 'rb') as handle:
    all_stocks_info = pickle.load(handle)


In [33]:
len(all_stocks_info)

84

In [34]:
all_return_table['2018-03-01']

datadate     gvkey  adj_price  daily_return
0   2017-03-01  164010.0   8.823208           NaN
1   2017-03-02  164010.0   8.842048      0.002135
2   2017-03-03  164010.0   8.835769     -0.000710
3   2017-03-06  164010.0   8.842048      0.000711
4   2017-03-07  164010.0   8.823208     -0.002131
..         ...       ...        ...           ...
247 2018-02-22  260774.0  44.779999      0.006745
248 2018-02-23  260774.0  45.950001      0.026128
249 2018-02-26  260774.0  46.639999      0.015016
250 2018-02-27  260774.0  47.070000      0.009220
251 2018-02-28  260774.0  46.750000     -0.006798

[62469 rows x 4 columns]

In [35]:
len(all_return_table)

84

In [36]:
all_stocks_info['2018-03-01']

gvkey  predicted_return  trade_date
0    164010          0.015036  2018-03-01
1    176622          0.024810  2018-03-01
2    178901          0.024220  2018-03-01
3      4430          0.026612  2018-03-01
4      6788          0.026612  2018-03-01
..      ...               ...         ...
245  113490          0.018267  2018-03-01
246  138743          0.018267  2018-03-01
247  160479          0.018267  2018-03-01
248  160991          0.018267  2018-03-01
249  260774          0.018267  2018-03-01

[250 rows x 3 columns]

# 4. Potfolio Optimization using pypfopt

In [37]:
# took under 5 minutes to run
from pypfopt import objective_functions
stocks_weight_table = pd.DataFrame([])

for i in range(len(trade_date)):
    # get selected stocks information
    p1_alldata=(all_stocks_info[trade_date[i]])
    # sort it by tic
    p1_alldata=p1_alldata.sort_values('gvkey')
    p1_alldata = p1_alldata.reset_index()
    del p1_alldata['index']
    
    print(p1_alldata)
    # get selected stocks tic
    p1_stock = p1_alldata.gvkey
    
    # get predicted return from selected stocks
    p1_predicted_return=p1_alldata.pivot_table(index = 'trade_date',columns = 'gvkey', values = 'predicted_return')
    # use the predicted returns as the Expected returns to feed into the portfolio object
    

    # get the 1-year historical return
    p1_return_table=all_return_table[trade_date[i]]
    p1_return_table_pivot=p1_return_table.pivot_table(index = 'datadate',columns = 'gvkey', values = 'daily_return')
    print(p1_return_table)
    selected_stocks = list(set(p1_predicted_return.columns).intersection(p1_return_table_pivot.columns))
    # use the 1-year historical return table to calculate covariance matrix between selected stocks
    p1_predicted_return = p1_predicted_return.loc[:, selected_stocks]
    p1_return_table_pivot = p1_return_table_pivot.loc[:, selected_stocks]
    S = risk_models.sample_cov(p1_return_table_pivot)
    mu = p1_predicted_return.T.values
   # del S.index.name 
    # mean variance
    ef_mean = EfficientFrontier(mu, S,weight_bounds=(0, 0.05))
    # raw_weights_mean = ef_mean.max_sharpe()
    raw_weights_mean = ef_mean.nonconvex_objective(
        objective_functions.sharpe_ratio,
        objective_args = (ef_mean.expected_returns, ef_mean.cov_matrix),
        weights_sum_to_one = True
    )
    cleaned_weights_mean = ef_mean.clean_weights()
    # print(f'output{cleaned_weights_mean}')
    #print(raw_weights_mean)
    #ef.portfolio_performance(verbose=True)
    #print("cleaned_weights_mean: ", cleaned_weights_mean)

    # minimum variance
    ef_min = EfficientFrontier([0]*len(mu), S,weight_bounds=(0, 0.05))
   # raw_weights_min = ef_min.max_sharpe()
    raw_weights_min = ef_min.nonconvex_objective(
        objective_functions.sharpe_ratio,
        objective_args = (ef_min.expected_returns, ef_min.cov_matrix),
        weights_sum_to_one = True
    )
    cleaned_weights_min = ef_min.clean_weights()
    #print(cleaned_weights_min)
    print("cleaned_weights_min: ", cleaned_weights_min)

    idx = np.isin(p1_alldata.gvkey, selected_stocks)
    p1_alldata["mean_weight"] = 0
    p1_alldata.loc[idx, 'mean_weight'] = list(cleaned_weights_mean.values())

    p1_alldata["min_weight"] = 0
    p1_alldata.loc[idx, 'min_weight'] = list(cleaned_weights_min.values())

    p1_alldata["equal_weight"] = 0
    p1_alldata.loc[idx, 'equal_weight'] = np.ones(len(cleaned_weights_mean)) / len(cleaned_weights_mean)
    # p1_alldata["mean_weight"] = 0
    # p1_alldata['mean_weight'][idx] = list(cleaned_weights_mean.values())
    # p1_alldata["min_weight"] = 0
    # p1_alldata['min_weight'][idx] = list(cleaned_weights_min.values())
    # p1_alldata["equal_weight"] = 0
    # p1_alldata['equal_weight'][idx] = np.ones(len(cleaned_weights_mean.values())) / len(cleaned_weights_mean.values())
    #ef.portfolio_performance(verbose=True)
    
    stocks_weight_table = pd.concat([stocks_weight_table, p1_alldata])
    print(trade_date[i], ": Done")


      gvkey  predicted_return  trade_date
0      1045          0.052594  2009-06-01
1      1161          0.098717  2009-06-01
2      1230          0.036450  2009-06-01
3      1661          0.062174  2009-06-01
4      1704          0.058399  2009-06-01
..      ...               ...         ...
139  178917          0.027077  2009-06-01
140  179534          0.111660  2009-06-01
141  180112          0.032765  2009-06-01
142  181699          0.023077  2009-06-01
143  260774          0.048888  2009-06-01

[144 rows x 3 columns]
      datadate     gvkey  adj_price  daily_return
0   2008-06-02  162353.0  87.959999           NaN
1   2008-06-03  162353.0  86.879997     -0.012278
2   2008-06-04  162353.0  86.650002     -0.002647
3   2008-06-05  162353.0  86.449997     -0.002308
4   2008-06-06  162353.0  89.059998      0.030191
..         ...       ...        ...           ...
246 2009-05-22  260774.0   6.770000     -0.021676
247 2009-05-26  260774.0   7.290000      0.076809
248 2009-05-27  260774

e:\ucb\code\capstone\FinRL-Trading\venv\Lib\site-packages\pypfopt\risk_models.py:70: UserWarning: The covariance matrix is non positive semidefinite. Amending eigenvalues.
  warnings.warn(
e:\ucb\code\capstone\FinRL-Trading\venv\Lib\site-packages\pypfopt\risk_models.py:89: UserWarning: Could not fix matrix. Please try a different risk model.
  warnings.warn(
C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2319351480.py:61: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[0.00699, 0.00696, 0.00696, 0.00698, 0.00698, 0.00697, 0.00692, 0.00699, 0.00699, 0.00701, 0.00692, 0.00695, 0.00692, 0.00696, 0.00695, 0.00695, 0.00692, 0.00695, 0.00695, 0.00696, 0.007, 0.00695, 0.007, 0.00701, 0.00696, 0.007, 0.007, 0.0071, 0.00702, 0.0071, 0.00694, 0.00705, 0.00698, 0.00695, 0.00701, 0.00698, 0.0071, 0.00705, 0.00694, 0.007, 0.00697, 0.00699, 0.00695, 0.00694, 0.00698, 0.00701, 0.00708, 0.007, 0.0, 0.00713, 0.00702, 0

cleaned_weights_min:  OrderedDict([(10247.0, 0.0069), (117768.0, 0.0069), (9225.0, 0.0069), (4108.0, 0.0069), (66065.0, 0.0069), (178707.0, 0.0069), (1045.0, 0.0069), (165914.0, 0.0069), (4640.0, 0.0069), (9248.0, 0.0069), (175138.0, 0.0069), (3107.0, 0.0069), (3619.0, 0.0069), (29736.0, 0.0069), (143912.0, 0.0069), (9777.0, 0.0069), (162353.0, 0.0069), (30259.0, 0.0069), (60979.0, 0.0069), (161844.0, 0.0069), (61494.0, 0.0069), (29241.0, 0.0069), (8253.0, 0.0069), (20548.0, 0.0069), (162887.0, 0.0069), (141384.0, 0.0069), (7241.0, 0.0069), (65609.0, 0.0069), (5709.0, 0.0069), (6733.0, 0.0069), (14418.0, 0.0069), (152149.0, 0.0069), (6742.0, 0.0069), (30822.0, 0.0069), (165993.0, 0.0069), (163946.0, 0.0069), (13421.0, 0.0069), (5742.0, 0.0069), (9846.0, 0.0069), (61567.0, 0.0069), (154755.0, 0.0069), (1161.0, 0.0069), (10894.0, 0.0069), (145552.0, 0.0069), (3735.0, 0.0069), (10903.0, 0.0069), (24216.0, 0.0069), (3226.0, 0.0069), (1690.0, 0.0069), (5786.0, 0.0069), (145049.0, 0.0069), (

C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2319351480.py:61: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[0.00864, 0.01268, 0.00794, 0.0, 0.00785, 0.00417, 0.0117, 0.00647, 0.0, 0.00487, 0.0, 0.00962, 0.00768, 0.00227, 0.00618, 0.00915, 0.00603, 0.00863, 0.00038, 0.01064, 0.00525, 0.01289, 0.00481, 0.0041, 0.00943, 0.00991, 0.01129, 0.00391, 0.00662, 0.00866, 0.00191, 0.00589, 0.00575, 0.00585, 0.00406, 0.00962, 0.01314, 0.0087, 0.00273, 0.00569, 0.00544, 0.01518, 0.005, 0.00843, 0.00523, 0.01068, 0.00554, 0.00176, 0.0, 0.00839, 0.0, 0.01233, 0.00492, 0.00703, 0.01271, 0.01289, 0.0, 0.00723, 0.00719, 0.0056, 0.00802, 0.0, 0.00801, 0.00846, 0.0, 0.00105, 0.0, 0.01436, 0.00886, 0.00202, 0.00792, 0.00225, 0.01001, 0.00898, 0.0, 0.0114, 0.00486, 0.00828, 0.01167, 0.0, 0.01202, 0.00765, 0.01072, 0.00732, 0.00345, 0.01063, 0.00344, 0.00961, 0.02102, 0.00627, 0.0143, 0.00268, 0.00498, 0.0007, 0.00552, 

cleaned_weights_min:  OrderedDict([(117768.0, 0.00546), (9225.0, 0.00546), (4108.0, 0.00546), (158742.0, 0.00546), (6682.0, 0.00546), (165914.0, 0.00546), (13341.0, 0.00546), (9248.0, 0.00546), (175138.0, 0.00546), (3619.0, 0.00546), (11811.0, 0.00546), (63527.0, 0.00546), (29736.0, 0.00546), (10793.0, 0.00546), (24617.0, 0.00546), (112168.0, 0.00546), (143912.0, 0.00546), (9777.0, 0.00546), (30259.0, 0.00546), (60979.0, 0.00546), (15414.0, 0.00546), (61494.0, 0.00546), (15417.0, 0.00546), (29241.0, 0.00546), (8253.0, 0.00546), (1598.0, 0.00546), (162887.0, 0.00546), (7241.0, 0.00546), (65609.0, 0.00546), (160329.0, 0.00546), (5709.0, 0.00546), (6733.0, 0.00546), (183377.0, 0.00546), (9299.0, 0.00546), (12884.0, 0.00546), (152149.0, 0.00546), (2136.0, 0.00546), (141913.0, 0.00546), (4199.0, 0.00546), (163946.0, 0.00546), (10860.0, 0.00546), (13421.0, 0.00546), (5742.0, 0.00546), (11376.0, 0.00546), (10867.0, 0.00546), (64630.0, 0.00546), (147579.0, 0.00546), (6268.0, 0.00546), (160893.

...

C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2319351480.py:61: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[0.00715, 0.0134, 0.00584, 0.0052, 0.0023, 0.00474, 0.02138, 0.01692, 0.0, 0.02266, 0.0, 0.00058, 0.0, 0.01734, 0.00292, 0.0164, 0.05, 0.0, 0.00173, 0.00479, 0.00137, 0.01776, 0.00575, 0.0, 0.0, 0.0, 0.00768, 0.00153, 0.01009, 0.0026, 0.0, 0.01488, 0.00799, 0.00836, 0.0, 0.0, 0.0, 0.00396, 0.00463, 0.00866, 0.0032, 0.0286, 0.00025, 0.00374, 0.0036, 0.00453, 0.01468, 0.00754, 0.00608, 0.0, 0.00165, 0.0, 0.00364, 0.00414, 0.0, 0.0, 0.00258, 0.01729, 0.00079, 0.00151, 0.0, 0.0, 0.00692, 0.01268, 0.0, 0.00022, 0.02368, 0.01378, 0.0, 0.02877, 0.01197, 0.0, 0.00207, 0.0116, 0.0, 0.04142, 0.00607, 0.00171, 0.0, 0.01482, 0.01368, 0.0, 0.01382, 0.0, 0.00375, 0.00851, 0.01123, 0.0, 0.0, 0.04999, 0.00931, 0.00218, 0.00489, 0.00893, 0.00217, 0.00018, 0.0, 0.0, 0.0, 0.00601, 0.00428, 0.02258, 0.0172, 0.0,

cleaned_weights_min:  OrderedDict([(117768.0, 0.00662), (9225.0, 0.00662), (2574.0, 0.00662), (66065.0, 0.00662), (1045.0, 0.00662), (158742.0, 0.00662), (6682.0, 0.00662), (165914.0, 0.00662), (9248.0, 0.00662), (3107.0, 0.00662), (3619.0, 0.00662), (29736.0, 0.00662), (24617.0, 0.00662), (9777.0, 0.00662), (60979.0, 0.00662), (144435.0, 0.00662), (9783.0, 0.00662), (29241.0, 0.00662), (28733.0, 0.00662), (4674.0, 0.00662), (6733.0, 0.00662), (11856.0, 0.00662), (30293.0, 0.00662), (14934.0, 0.00662), (16478.0, 0.00662), (1632.0, 0.00662), (110179.0, 0.00662), (30822.0, 0.00662), (31846.0, 0.00662), (65640.0, 0.00662), (165993.0, 0.00662), (163946.0, 0.00662), (5742.0, 0.00662), (9846.0, 0.00662), (119417.0, 0.00662), (147579.0, 0.00662), (1661.0, 0.00662), (4737.0, 0.00662), (154755.0, 0.00662), (1161.0, 0.00662), (1678.0, 0.00662), (10894.0, 0.00662), (145049.0, 0.00662), (5786.0, 0.00662), (9882.0, 0.00662), (24731.0, 0.00662), (175263.0, 0.00662), (15520.0, 0.00662), (10405.0, 0.0

C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2319351480.py:61: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[0.00281, 0.00438, 0.00668, 0.01119, 0.00682, 0.0, 0.00746, 0.02281, 0.0, 0.0, 0.00828, 0.00417, 0.01673, 0.00069, 0.00276, 0.00667, 0.01667, 0.02042, 0.0, 0.00146, 0.01882, 0.0, 0.0114, 0.01052, 0.0, 0.01334, 0.0, 0.0, 0.01225, 0.0, 0.01395, 0.0, 0.0, 0.00968, 0.0, 0.00096, 0.0, 0.0, 0.0304, 0.03907, 0.004, 0.0, 0.0, 0.0, 0.00429, 0.00461, 0.01043, 0.01172, 0.00128, 0.0, 0.01053, 0.0, 0.02188, 0.0, 0.0, 0.00379, 0.01479, 0.00691, 0.00117, 0.00324, 0.0, 0.0, 0.0, 0.00534, 0.02151, 0.00645, 0.0, 0.01095, 0.0, 0.00692, 0.00196, 0.0, 0.0041, 0.01788, 0.01141, 0.0, 0.0, 0.0, 0.00372, 0.0, 0.0, 0.01689, 0.0, 0.02195, 0.03219, 0.00192, 0.0, 0.0, 0.04985, 0.0, 0.00323, 0.01738, 0.03963, 0.00519, 0.01273, 0.0, 0.0, 0.01041, 0.0, 0.0, 0.0, 0.00493, 0.00152, 0.0, 0.01075, 0.00338, 0.0, 0.00569, 0.00197

cleaned_weights_min:  OrderedDict([(7171.0, 0.00645), (117768.0, 0.00645), (4108.0, 0.00645), (2574.0, 0.00645), (165914.0, 0.00645), (3619.0, 0.00645), (11811.0, 0.00645), (29736.0, 0.00645), (24617.0, 0.00645), (143912.0, 0.00645), (5680.0, 0.00645), (1075.0, 0.00645), (30259.0, 0.00645), (13365.0, 0.00645), (144435.0, 0.00645), (15417.0, 0.00645), (29241.0, 0.00645), (1602.0, 0.00645), (3650.0, 0.00645), (162887.0, 0.00645), (3144.0, 0.00645), (6216.0, 0.00645), (6730.0, 0.00645), (65609.0, 0.00645), (160329.0, 0.00645), (5709.0, 0.00645), (149070.0, 0.00645), (177227.0, 0.00645), (9299.0, 0.00645), (152149.0, 0.00645), (141400.0, 0.00645), (7257.0, 0.00645), (146017.0, 0.00645), (3170.0, 0.00645), (110179.0, 0.00645), (163946.0, 0.00645), (10860.0, 0.00645), (5229.0, 0.00645), (5742.0, 0.00645), (13421.0, 0.00645), (11376.0, 0.00645), (6266.0, 0.00645), (6781.0, 0.00645), (61567.0, 0.00645), (6788.0, 0.00645), (5256.0, 0.00645), (1161.0, 0.00645), (141459.0, 0.00645), (145046.0, 0.

C:\Users\misss\AppData\Local\Temp\ipykernel_40368\2319351480.py:61: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[0.0, 0.00149, 0.01334, 0.00298, 0.0, 0.0, 0.0, 0.00735, 0.00157, 0.0, 0.01066, 0.0, 0.0116, 0.01284, 0.00388, 0.0, 0.0, 0.0, 0.04997, 0.0, 0.0, 0.00471, 0.0, 0.01224, 0.00435, 0.01154, 0.00615, 0.00905, 0.0, 0.0, 0.00693, 0.00846, 0.0, 0.00312, 0.00944, 0.00232, 0.0, 0.0, 0.00201, 0.0, 0.0, 0.00127, 0.00648, 0.04997, 0.01307, 0.01614, 0.0, 0.00366, 0.00327, 0.0, 0.00019, 0.00369, 0.01116, 0.00457, 0.01324, 0.00169, 0.0, 0.00723, 0.00143, 0.00542, 0.03003, 0.0, 0.0, 0.0, 0.00894, 0.00094, 0.0, 0.01215, 0.0, 0.0, 0.01661, 0.00781, 0.0, 0.0, 0.00574, 0.01003, 0.00439, 0.00624, 0.01524, 0.01386, 0.00344, 0.00513, 0.0, 0.0, 0.00987, 0.0137, 0.00932, 0.03398, 0.00248, 0.00594, 0.00201, 0.00456, 0.0, 0.0, 0.00108, 0.0, 0.0, 0.00028, 0.0, 0.00079, 0.00104, 0.02323, 0.0, 0.00441, 0.00464, 0.0, 0.0056

In [38]:
stocks_weight_table.shape

(16425, 6)

In [39]:
stocks_weight_table.head()

gvkey  predicted_return  trade_date  mean_weight  min_weight  equal_weight
0   1045          0.052594  2009-06-01      0.00699     0.00694      0.006944
1   1161          0.098717  2009-06-01      0.00696     0.00694      0.006944
2   1230          0.036450  2009-06-01      0.00696     0.00694      0.006944
3   1661          0.062174  2009-06-01      0.00698     0.00694      0.006944
4   1704          0.058399  2009-06-01      0.00698     0.00694      0.006944

## save to excel or csv

In [40]:
df_mean = pd.DataFrame()
df_mean['trade_date'] = stocks_weight_table['trade_date']
df_mean['gvkey'] = stocks_weight_table['gvkey']
df_mean['weights'] = stocks_weight_table['mean_weight']
df_mean['predicted_return'] = stocks_weight_table['predicted_return']
df_mean.to_excel("mean_weighted.xlsx")

In [41]:
df_min = pd.DataFrame()
df_min['trade_date'] = stocks_weight_table['trade_date']
df_min['gvkey'] = stocks_weight_table['gvkey']
df_min['weights'] = stocks_weight_table['min_weight']
df_min['predicted_return'] = stocks_weight_table['predicted_return']
df_min.to_excel("minimum_weighted.xlsx")

In [42]:
df_equal = pd.DataFrame()
df_equal['trade_date'] = stocks_weight_table['trade_date']
df_equal['gvkey'] = stocks_weight_table['gvkey']
df_equal['weights'] = stocks_weight_table['equal_weight']
df_equal['predicted_return'] = stocks_weight_table['predicted_return']
df_equal.to_excel("equally_weighted.xlsx")